## WaveNet声码器 

In [1]:
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "3"

import torch
import librosa
import pickle
from synthesis import build_model
from synthesis import wavegen
from pydub import AudioSegment

output_dir="./output/"
spect_vc = pickle.load(open('results.pkl', 'rb'))
device = torch.device("cuda")

model = build_model().to(device)
#This model is WaveNet Model
checkpoint = torch.load("checkpoint_step001000000_ema.pth")
model.load_state_dict(checkpoint["state_dict"])

for spect in spect_vc:
    name = spect[0]
    c = spect[1]
    print(name)
    waveform = wavegen(model, c=c)   
    librosa.output.write_wav(output_dir+name+'.wav', waveform, sr=16000)


  0%|          | 0/109824 [00:00<?, ?it/s]

U1xH1


  0%|          | 0/109824 [00:00<?, ?it/s]

U1xL1


  0%|          | 0/48384 [00:00<?, ?it/s]

...

  0%|          | 0/43264 [00:00<?, ?it/s]

U11xH1


  0%|          | 0/43264 [00:00<?, ?it/s]

U11xL1


100%|██████████| 43264/43264 [07:38<00:00, 94.38it/s] 


## Griffin-Lim声码器（效果不好） 

In [ ]:
import scipy.signal as signal
import librosa
import numpy as np
import pickle
import copy
from pydub import AudioSegment

# DVC: n_fft=512, win_length=400, hop_length=80, num_iters=60
# AUTOVC: fft_length=1024, hop_length=256
def _mel_to_linear_matrix(sr, n_fft, n_mels):
    m = librosa.filters.mel(sr, n_fft, n_mels)
    m_t = np.transpose(m)
    p = np.matmul(m, m_t)
    d = [1.0 / x if np.abs(x) > 1.0e-8 else x for x in np.sum(p, axis=0)]
    return np.matmul(m_t, np.diag(d))
def invert_spectrogram(spectrogram):
    '''
    spectrogram: [f, t]
    '''
    return librosa.istft(spectrogram, hop_length, win_length=win_length, window="hann")
def griffin_lim(spectrogram):
    '''Applies Griffin-Lim's raw.
    '''
    X_best = copy.deepcopy(spectrogram)
    for i in range(n_iter):
        X_t = invert_spectrogram(X_best)
        est = librosa.stft(X_t, n_fft, hop_length, win_length=win_length)
        phase = est / np.maximum(1e-8, np.abs(est))
        X_best = spectrogram * phase
    X_t = invert_spectrogram(X_best)
    y = np.real(X_t)

    return y
def melspectrogram2wav(mel):
    '''# Generate wave file from spectrogram'''
    # transpose
    mel = mel.T

    # de-noramlize
    mel = (np.clip(mel, 0, 1) * max_db) - max_db + ref_db

    # to amplitude
    mel = np.power(10.0, mel * 0.05)
    m = _mel_to_linear_matrix(sr, n_fft, n_mels)
    mag = np.dot(m, mel)

    # wav reconstruction
    wav = griffin_lim(mag)

    # de-preemphasis
    wav = signal.lfilter([1], [1, -preemphasis], wav)

    # trim
    wav, _ = librosa.effects.trim(wav)

    return wav.astype(np.float32)

max_db = 100
ref_db = 0
sr = 16000
n_fft = 1024
n_mels = 80
n_iter= 60
preemphasis = 1 # or None
# frame_shift = 0.0125 # seconds
# frame_length = 0.05 # seconds
hop_length = 256 # samples.
win_length = 1024 # samples.

output_dir="./output/"
spect_vc = pickle.load(open('results.pkl', 'rb'))

for spect in spect_vc:
    name = spect[0]
    c = spect[1]
    print(name)
    waveform = melspectrogram2wav(mel=c)
#     librosa.output.write_wav(output_dir+name+'.wav', waveform, sr=16000)

In [2]:
from IPython.display import Audio

display(Audio('./output/U1xH1.wav'))
display(Audio('./output/U1xL1.wav'))
display(Audio('./output/U2xH1.wav'))
display(Audio('./output/U2xL1.wav'))
display(Audio('./output/U3xH1.wav'))
display(Audio('./output/U3xL1.wav'))
display(Audio('./output/U4xH1.wav'))
display(Audio('./output/U4xL1.wav'))
display(Audio('./output/U5xH1.wav'))
display(Audio('./output/U5xL1.wav'))
display(Audio('./output/U6xH1.wav'))
display(Audio('./output/U6xL1.wav'))
display(Audio('./output/U7xH1.wav'))
display(Audio('./output/U7xL1.wav'))
display(Audio('./output/U8xH1.wav'))
display(Audio('./output/U8xL1.wav'))
display(Audio('./output/U9xH1.wav'))
display(Audio('./output/U9xL1.wav'))
display(Audio('./output/U10xH1.wav'))
display(Audio('./output/U10xL1.wav'))


In [3]:
import torch
# import torchvision
print(torch.cuda.is_available())
a = torch.Tensor(5,3)
a=a.cuda()
print(a)

True
tensor([[5.6719e-11, 7.3471e+28, 2.6383e+23],
        [2.7376e+20, 1.8040e+28, 1.8750e-19],
        [7.3909e+22, 2.4176e-12, 2.6209e+20],
        [4.1641e+12, 8.9625e-01, 7.9309e+34],
        [7.9439e+08, 3.2604e-12, 7.3113e+34]], device='cuda:0')
